In [9]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%run _0_All_functions.ipynb as func

In [10]:
data_path='/Users/sananaz/Desktop/Study2/AIML/GL_python/10_Capstone/input_data.xlsx'
desc_col='Short description'

In [11]:
df=pd.read_excel(data_path)

https://turbolab.in/text-classification-using-machine-learning/

https://turbolab.in/text-classification-with-keras-and-glove-word-embeddings/

In [12]:
from nltk.stem.snowball import SnowballStemmer
from nltk.corpus import stopwords
import string, re
stemmer = SnowballStemmer('english') # stemmer
t = str.maketrans(dict.fromkeys(string.punctuation)) # special char removal

In [13]:
#Data cleaning 
from nltk.corpus import stopwords
import re
#lower case, only alphabets, remove spaces, remove stopwords
df['text_clean'] = df[desc_col].apply(lambda x: str(x).lower())
df['text_clean'] = df['text_clean'].apply(lambda x: re.sub('[^a-zA-z0-9_\s]','',str(x)))
stopwords = set(stopwords.words('english'))
df['text_clean'] = df['text_clean'].apply(lambda x: ' '.join([stemmer.stem(word) for word in x.split() if word not in stopwords]))
df['text_clean'] = df['text_clean'].apply(lambda x: str(x).strip())

                                                                    

In [14]:
df['Length']=df['text_clean'].apply(lambda x: len(x))
df=df[df["Length"]!=0]
df.shape

(8453, 6)

In [15]:
df['Group_no']=df["Assignment group"]
#.apply(lambda x: x.split('_')[1])

In [8]:
df.query('Group_no in ["GRP_0","GRP_8","GRP_24","GRP_12","GRP_9","GRP_2","GRP_19","GRP_3","GRP_6","GRP_13"]',inplace=True)
         
         #,10,5,14,25,33,4"]',inplace=True)

In [164]:
df.Group_no.unique()

array(['0', '3', '6', '8', '9', '12', '13', '19', '2', '24'], dtype=object)

In [165]:
df['Group_no']=df["Assignment group"].apply(lambda x: x.split('_')[1])

In [166]:
df.head()

Short description  \
0                    login issue   
1                        outlook   
2             cant log in to vpn   
3  unable to access hr_tool page   
4                   skype error    

                                         Description             Caller  \
0  -verified user details.(employee# & manager na...  spxjnwir pjlcoqds   
1  \r\n\r\nreceived from: hmjdrvpb.komuaywn@gmail...  hmjdrvpb komuaywn   
2  \r\n\r\nreceived from: eylqgodm.ybqkwiam@gmail...  eylqgodm ybqkwiam   
3                      unable to access hr_tool page  xbkucsvz gcpydteq   
4                                       skype error   owlgqjme qhcozdfx   

  Assignment group                 text_clean  Length Group_no  
0            GRP_0                 login issu      10        0  
1            GRP_0                    outlook       7        0  
2            GRP_0               cant log vpn      12        0  
3            GRP_0  unabl access hr_tool page      25        0  
4            GRP_0                skype error      11        0

In [167]:
df=df[df["Length"]!=0]

Attributes
----------
cluster_centers_ : ndarray of shape (n_clusters, n_features)
    Coordinates of cluster centers. If the algorithm stops before fully
    converging (see ``tol`` and ``max_iter``), these will not be
    consistent with ``labels_``.

labels_ : ndarray of shape (n_samples,)
    Labels of each point

inertia_ : float
    Sum of squared distances of samples to their closest cluster center,
    weighted by the sample weights if provided.

n_iter_ : int
    Number of iterations run.

n_features_in_ : int
    Number of features seen during :term:`fit`.

    .. versionadded:: 0.24

feature_names_in_ : ndarray of shape (`n_features_in_`,)
    Names of features seen during :term:`fit`. Defined only when `X`
    has feature names that are all strings.

In [168]:
from sklearn import model_selection, preprocessing
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
'''Assume df is the dataset with columns "content" and "label"'''
# split the data into training and validation
train_x, valid_x, train_y, valid_y = model_selection.train_test_split(df['text_clean'], df['Assignment group'])
# label encode the target variable 
encoder = preprocessing.LabelEncoder()
train_y = encoder.fit_transform(train_y)
valid_y = encoder.fit_transform(valid_y)
# count vectorization 
count_vect = CountVectorizer(analyzer='word', token_pattern=r'\w{1,}')
count_vect.fit(df['text_clean'])
xtrain_count = count_vect.transform(train_x)
xvalid_count = count_vect.transform(valid_x)
# word level tf-idf vectorization
tfidf_vect = TfidfVectorizer(analyzer='word', token_pattern=r'\w{1,}', max_features=5000)
tfidf_vect.fit(df['text_clean'])
xtrain_tfidf = tfidf_vect.transform(train_x)
xvalid_tfidf = tfidf_vect.transform(valid_x)
# ngram level tf-idf vectorization
tfidf_vect_ngram = TfidfVectorizer(analyzer='word', token_pattern=r'\w{1,}', ngram_range=(2,3), max_features=5000)
tfidf_vect_ngram.fit(df['text_clean'])
xtrain_tfidf_ngram = tfidf_vect_ngram.transform(train_x)
xvalid_tfidf_ngram = tfidf_vect_ngram.transform(valid_x)


In [169]:
from sklearn import linear_model, naive_bayes, svm, metrics
from sklearn.metrics import classification_report

target_names = list(encoder.classes_) # output labels for report generation
def report_generation(classifier, train_data, valid_data, train_y, valid_y):
   classifier.fit(train_data, train_y)
   predictions = classifier.predict(valid_data)
   print("Accuracy :", metrics.accuracy_score(predictions, valid_y))
   report = classification_report(valid_y, predictions, output_dict=True, target_names=target_names)
   return report

In [170]:
# Naive Bayes
classifier = naive_bayes.MultinomialNB()
report = report_generation(classifier, xtrain_count, xvalid_count, train_y, valid_y)
print("NB Count Vectorizer Report :", report['weighted avg'])


Accuracy : 0.7981308411214953
NB Count Vectorizer Report : {'precision': 0.7726473432307135, 'recall': 0.7981308411214953, 'f1-score': 0.747576228092831, 'support': 1605}


In [171]:
report = report_generation(classifier, xtrain_tfidf, xvalid_tfidf, train_y, valid_y)
print("NB TFIDF-Word Report :", report['weighted avg'])


Accuracy : 0.746417445482866
NB TFIDF-Word Report : {'precision': 0.6785103485946742, 'recall': 0.746417445482866, 'f1-score': 0.6593079495503701, 'support': 1605}


/Users/sananaz/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/sananaz/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/sananaz/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [172]:
report = report_generation(classifier, xtrain_tfidf_ngram, xvalid_tfidf_ngram, train_y, valid_y)
print("NB TFIDF-NGram Report :", report['weighted avg'])


Accuracy : 0.7507788161993769
NB TFIDF-NGram Report : {'precision': 0.7043470982697416, 'recall': 0.7507788161993769, 'f1-score': 0.6770224873254466, 'support': 1605}


/Users/sananaz/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/sananaz/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/sananaz/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [173]:
classifier = linear_model.LogisticRegression()    
report = report_generation(classifier, xtrain_count, xvalid_count, train_y, valid_y)    
print("LogisticRegression Count Vectorizer Report :", report['weighted avg'])


Accuracy : 0.8274143302180685
LogisticRegression Count Vectorizer Report : {'precision': 0.8193238219765755, 'recall': 0.8274143302180685, 'f1-score': 0.8015663776304965, 'support': 1605}


In [15]:
from nltk.tokenize import RegexpTokenizer
import numpy as np
import re

In [16]:
def _to_words(comp):
    
    words = RegexpTokenizer('\w+').tokenize(comp)
    words = [re.sub(r'([xx]+)|([XX]+)|(\d+)', '', w).lower() for w in words]
    words = list(filter(lambda a: a != '', words))
    
    return words

In [17]:
#Get Vocabulary

In [18]:
all_words = list()
for comp in df['text_clean']:
    for w in _to_words(comp):
        all_words.append(w)

In [19]:
print('Size of vocabulary: {}'.format(len(set(all_words))))

Size of vocabulary: 6260


In [35]:
for i in range(10):
    print('text\n', df['text_clean'][i], '\n')
    print('Tokens\n', _to_words(df['text_clean'][i]))

text
 login issue 

Tokens
 ['login', 'issue']
text
 outlook 

Tokens
 ['outlook']
text
 cant log vpn 

Tokens
 ['cant', 'log', 'vpn']
text
 unable access hr_tool page 

Tokens
 ['unable', 'access', 'hr_tool', 'page']
text
 skype error 

Tokens
 ['skype', 'error']
text
 unable log engineering tool skype 

Tokens
 ['unable', 'log', 'engineering', 'tool', 'skype']
text
 event criticalhostname_221companycom value mountpoint threshold oraclesid_37erpdata21 

Tokens
 ['event', 'criticalhostname_companycom', 'value', 'mountpoint', 'threshold', 'oraclesid_erpdata']
text
 ticket_no1550391 employment status new nonemployee [enter users name] 

Tokens
 ['ticket_no', 'employment', 'status', 'new', 'nonemployee', 'enter', 'users', 'name']
text
 unable disable add ins outlook 

Tokens
 ['unable', 'disable', 'add', 'ins', 'outlook']
text
 ticket update inplant_874773 

Tokens
 ['ticket', 'update', 'inplant_']


In [21]:
#Indexing

In [39]:
index_dict = dict()
count = 1
index_dict['<unk>'] = 0
for word in set(all_words):
    index_dict[word] = count
    count += 1
len(index_dict)

6261

In [ ]:
#Embedding

In [51]:
#https://turbolab.in/text-classification-with-keras-and-glove-word-embeddings/

In [23]:
import gensim 
from gensim.scripts.glove2word2vec import glove2word2vec 
from gensim.test.utils import datapath, get_tmpfile 

glove_file = datapath('glove.6B.300d.txt') 
glove_file_new_format = get_tmpfile('test_word2vec')

In [24]:
glove_file

'/Users/sananaz/anaconda3/lib/python3.7/site-packages/gensim/test/test_data/glove.6B.300d.txt'

In [25]:
embeddings_index = {}
f = open('glove_file') # GLOBAL VECTOR
for line in f:
    values = line.split()
    word = values[0]
    coefs = np.asarray(values[1:], dtype='float32')
    embeddings_index[word] = coefs
f.close()

In [50]:
embeddings_index.get(1)

In [27]:
def find_similar_word(emmbedes):
  nearest = sorted(embeddings_index.keys(), key=lambda word: spatial.distance.euclidean(embeddings_index[word], emmbedes))
  return nearest

In [41]:
find_similar_word(embeddings_index[0:10])#[0:10]

TypeError: unhashable type: 'slice'

In [28]:
data_list = list()
for comp in df['text_clean']:
    sentence = np.zeros(300)
    count = 0
    for w in _to_words(comp):
        try:
            sentence += embeddings_index[w]
            count += 1
        except KeyError:
            continue
    data_list.append(sentence / count)

/Users/sananaz/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:11: RuntimeWarning: invalid value encountered in true_divide
  # This is added back by InteractiveShellApp.init_path()


In [33]:
data_list

[array([-0.00973   ,  0.152965  ,  0.08967501, -0.124469  ,  0.42726049,
         0.1103475 ,  0.0731145 , -0.025689  ,  0.10090999, -0.87726994,
        -0.07468499,  0.074379  ,  0.13453   , -0.30220999, -0.42571498,
        -0.11848499, -0.32466   ,  0.120135  ,  0.020985  , -0.128236  ,
        -0.08866001,  0.46399499, -0.25437   , -0.1639475 , -0.04901499,
        -0.11213501,  0.32195999,  0.19729   ,  0.41419502, -0.0252895 ,
         0.30979999, -0.17236499, -0.2390595 ,  0.21530999, -0.30770001,
        -0.23559999, -0.0653495 ,  0.322115  , -0.35814501,  0.112755  ,
         0.07712999, -0.0772    ,  0.37693501,  0.02019   , -0.32049   ,
         0.25805499, -0.50336999,  0.16719499, -0.83158001,  0.11567499,
         0.11659   ,  0.002565  , -0.35415999, -0.267618  ,  0.029705  ,
         0.210082  , -0.06638999,  0.21891   , -0.45849002, -0.208785  ,
         0.40456001, -0.29542001, -0.123884  , -0.07743499,  0.23892999,
        -0.281935  ,  0.33386499,  0.0889305 ,  0.4

In [30]:
from sklearn import preprocessing
le = preprocessing.LabelEncoder()
le.fit(df['Assignment group'])
df['Target'] = le.transform(df['Assignment group'])
df.head()

Short description  \
0                    login issue   
1                        outlook   
2             cant log in to vpn   
3  unable to access hr_tool page   
4                   skype error    

                                         Description             Caller  \
0  -verified user details.(employee# & manager na...  spxjnwir pjlcoqds   
1  \r\n\r\nreceived from: hmjdrvpb.komuaywn@gmail...  hmjdrvpb komuaywn   
2  \r\n\r\nreceived from: eylqgodm.ybqkwiam@gmail...  eylqgodm ybqkwiam   
3                      unable to access hr_tool page  xbkucsvz gcpydteq   
4                                       skype error   owlgqjme qhcozdfx   

  Assignment group                  text_clean  Length  Target  
0            GRP_0                 login issue      11       0  
1            GRP_0                     outlook       7       0  
2            GRP_0                cant log vpn      12       0  
3            GRP_0  unable access hr_tool page      26       0  
4            GRP_0                 skype error      11       0

In [ ]:
from sklearn.decomposition import IncrementalPCA    # inital reduction
from sklearn.manifold import TSNE                   # final reduction
import numpy as np                                  # array handling

def display_closestwords_tsnescatterplot(model, dim, words):
    
    arr = np.empty((0,dim), dtype='f')
    word_labels = words

    # get close words
    #close_words = [model.similar_by_word(word) for word in words]
    
    # add the vector for each of the closest words to the array
    close_words=[]
    for word in words:
        arr = np.append(arr, np.array([model[word]]), axis=0)
        close_words +=model.similar_by_word(word)
        
    for wrd_score in close_words:
        wrd_vector = model[wrd_score[0]]
        word_labels.append(wrd_score[0])
        arr = np.append(arr, np.array([wrd_vector]), axis=0)
        
    # find tsne coords for 2 dimensions
    tsne = TSNE(n_components=2, random_state=0)
    #np.set_printoptions(suppress=True)
    Y = tsne.fit_transform(arr)

    x_coords = Y[:, 0]
    y_coords = Y[:, 1]
    # display scatter plot
    plt.scatter(x_coords, y_coords)

    for label, x, y in zip(word_labels, x_coords, y_coords):
        plt.annotate(label, xy=(x, y), xytext=(0, 0), textcoords='offset points')
    plt.xlim(x_coords.min()+0.00005, x_coords.max()+0.00005)
    plt.ylim(y_coords.min()+0.00005, y_coords.max()+0.00005)
    plt.show()
    
def tsne_plot(model, words):
    "Creates and TSNE model and plots it"
    labels = []
    tokens = []

    #for word in model.wv.vocab:
    for word in words:
        tokens.append(model[word])
        labels.append(word)
    
    tsne_model = TSNE(perplexity=40, n_components=2, init='pca', n_iter=2500, random_state=23)
    new_values = tsne_model.fit_transform(tokens)

    x = []
    y = []
    for value in new_values:
        x.append(value[0])
        y.append(value[1])
        
    plt.figure(figsize=(14, 10)) 
    for i in range(len(x)):
        plt.scatter(x[i],y[i])
        plt.annotate(labels[i],
                     xy=(x[i], y[i]),
                     xytext=(5, 2),
                     textcoords='offset points',
                     ha='right',
                     va='bottom')
    plt.show()